In [63]:
from utils import *
from ecDNA import *
from abcomputation import *
import numpy as np
import plotly.graph_objects as go

In [132]:
from utils import scatter_joint_marginal

In [211]:
referenceP4 = load_yaml('data/cell_counts_p4.yaml')
referenceP15 = load_yaml('data/cell_counts_p15.yaml')

In [ ]:
abc_results = load_yaml('runs/double/10K/total/results.yaml')

In [61]:
abc_results.keys()

dict_keys(['distances', 'distancesP15', 'distancesP4', 'num_samples', 'sampled_s', 'sampled_start', 'simulated_data_P1', 'simulated_data_P4'])

In [60]:
distances = abc_results['distances']
distancesP4 = abc_results['distancesP4']
distancesP15 = abc_results['distancesP15']

sampled_s = abc_results['sampled_s']
sampled_start = abc_results['sampled_start']

simulated_data_P4 = abc_results['simulated_data_P4']
simulated_data_P15 = abc_results['simulated_data_P1']

num_samples = abc_results['num_samples']

fitness = 'log'

In [62]:
print('average distance P4:', np.mean(distancesP4))
print('average distance P15:', np.mean(distancesP15))
print('average distance:', np.mean(distances))


average distance P4: 56.17866211126761
average distance P15: 228.7145571049918
average distance: 226.7146027750311


In [158]:
top_results = {'top_distancesP4': top_distancesP4,
               'top_distancesP15': top_distancesP15,
               'top_distances': top_distances,
               'top_s': top_s,
               'top_start': top_start,
               'top_simulated_data_P4': top_simulated_data_P4,
               'top_simulated_data_P15': top_simulated_data_P15,
               'top_percent': top_percent,
               'num_samples': num_samples}
save_yaml(dictionary=top_results, file_path='runs/double/10K/total/topresults.yaml')

Dictionary saved as yaml file to runs/double/10K/total/topresults.yaml


In [156]:
# Fonction pour la normalisation par z-score
def standard_score(distances):
    mean = float(np.mean(distances))
    std = float(np.std(distances))
    return [(d - mean) / std for d in distances]

# Normalisation des deux listes de distances
normalized_distancesP4 = standard_score(distancesP4)
normalized_distancesP15 = standard_score(distancesP15)

# Combinaison des distances normalisées
global_distances = [(d4 + d15) / 2 for d4, d15 in zip(normalized_distancesP4, normalized_distancesP15)]

# Affichage des résultats
print("Distances normalisées pour P4:", normalized_distancesP4)
print("Distances normalisées pour P15:", normalized_distancesP15)
print("Distances globales combinées:", global_distances)


Distances normalisées pour P4: [-0.45990242362222444, -0.12997242643285747, -0.2843541299723414, 0.00960881918900516, 1.2435249244074447, -0.5010777618849783, -0.9336406556301036, 0.0550874256496703, 0.0976571040839895, -0.05814791898561948, -0.7626760970736063, 0.1315236482606259, 0.23016938479401336, 0.2667096911677729, 0.18624933487007894, 0.136797558422211, 0.08330166252308258, -0.36714615879773577, 1.417078971853992, -0.49056691522617596, -0.7910558826964857, -0.9041799732425965, -0.9539132158741644, 0.0783588498604313, -1.0460732387237124, 0.012491432625396141, 0.1575857513909701, 0.13112160129763487, 0.2077363634049986, -0.48088847565976384, -0.8572300814169512, 0.1209994777588082, 0.40281807710766215, -1.106778666078493, -0.1741266428977878, 0.33219404791611495, -0.6253882179307744, -0.6431262501372261, -0.26066133922621837, -0.6494880520810214, -0.753977293064902, 2.5360223033079277, -0.1801100476999449, 0.977086370147385, -0.8988674239362658, -0.9341842684251326, -1.054475254

In [195]:
plot_histograms(data=[normalized_distancesP4, normalized_distancesP15],
                binsize=0.2, opacity=(1,0.7), colors=('#FF0080','#FFC100'),
                labels=('normalized distances P4', 'normalized distances P15'),
                title='Histogram of normalized distances at P4 and P15 (mean 0 and variance 1)',
                xaxis_title='normalized distance')

In [196]:
title = f'Histograms of Wasserstein distances at P4 and P15 ({num_samples} samples)'
xaxis_title = 'distance'
plot_histograms(data=[distancesP4, distancesP15], 
                binsize=20, opacity=(1,0.7), colors=('#FF0080','#FFC100'), 
                labels=('distances P4', 'distances P15'), 
                title=title, xaxis_title=xaxis_title)

In [157]:
top_percent = 5
smallest_indices = get_best_indices(global_distances, top_percent)

top_simulated_data_P4, top_simulated_data_P15 = [], []
top_distancesP4, top_distancesP15 = [], []
top_s, top_start = [], []
top_distances = []

# use one single for loop
for i in smallest_indices:
    top_simulated_data_P4.append(simulated_data_P4[i])
    top_simulated_data_P15.append(simulated_data_P15[i])
    top_s.append(sampled_s[i])
    top_start.append(sampled_start[i])
    top_distances.append(global_distances[i])
    top_distancesP4.append(normalized_distancesP4[i])
    top_distancesP15.append(normalized_distancesP15[i])

In [ ]:
# Load true data ------------------------------------------------------------------------------------------------------
file_path_p4 = 'data/cell_counts_p4.yaml'
true_data = load_yaml(file_path_p4)

In [212]:
plot_histograms_dict_overlay(dictionaries=[top_simulated_data_P4[0]],
                                true_data=referenceP4,
                                plot_ref=True,
                                labels=['Simulation'],
                                colors=['turquoise'],
                                title=f'Normalized distributions of ecDNA counts at passage 4 and simulation with {fitness} fitness (s={top_s[0]:.3f}, start P{top_start[0]}, score={top_distances[0]:.1f})',
                                save=True,
                                filepath='plots/bestsimulationp4.png')

plot_histograms_dict_overlay(dictionaries=[top_simulated_data_P15[0]],
                                true_data=referenceP15,
                                plot_ref=True,
                                labels=['Simulation'],
                                colors=['turquoise'],
                                title=f'Normalized distributions of ecDNA counts at passage 15 and simulation with {fitness} fitness (s={top_s[0]:.3f}, start P{top_start[0]}, score={top_distances[0]:.1f})',
                                save=True,
                                filepath='plots/bestsimulationp15.png')

In [208]:
from utils import plot_histograms_dict_overlay
for idx in range(10):
    plot_histograms_dict_overlay(dictionaries=[referenceP4, top_simulated_data_P4[idx], referenceP15, top_simulated_data_P15[idx]],
                                labels=['ref P4', 'simulation P4', 'ref P15', 'simulation P15'],
                                colors=['palegreen', 'lightskyblue', 'chartreuse', 'aquamarine'],
                                opacity=[0.5, 0.5, 0.5, 0.5],
                                title=f's = {top_s[idx]:.3f}, starting point = {top_start[idx]}, score P4 = {top_distancesP4[idx]:.2f}, score P15 = {top_distancesP15[idx]:.2f}, total score = {top_distances[idx]:.2f}',
                                )

In [70]:
metric = 'normalized'
plot_best_points_util(sampled_s, global_distances, metric, top_percent=5, save=True, filepath='plots/best_points.png')

In [144]:
scatter_joint_marginal(sampled_s,sampled_start, 's', 'start', title='Scatter plot of sampled parameters with marginals')

In [143]:
scatter_joint_marginal(top_s, top_start, 's', 'start', f'Scatter plot of {top_percent}% best sampled parameters with marginals (over {num_samples} samples)', info=global_distances, infolabel='distance', width=700, height=700, save=True, filepath='plots/jointmarginal.png')

In [131]:
plot_histograms_grouped(top_s, top_start, 's', 'start', 
                     title=f'Posterior distributions of s grouped by starting passage, {top_percent}% best over {num_samples} samples', 
                     save=True, width=800, height=1300, filepath='plots/histogramsgrouped.png')

In [206]:
plot_histograms_dict_overlay(dictionaries=top_simulated_data_P4,
                             true_data=referenceP4, bin_size=10,
                             plot_ref=True, true_label='Reference at P4',
                             title=f'ecDNA counts at passage 4 and {top_percent}% best simulations (over {num_samples} samples) with {fitness} fitness',
                             plot_avg=True, avg_color='red',
                             confidence_level=5, CI_linecolor='orangered', CI_fillcolor='rgba(206, 255, 79, 0.2)',
                             plot_all=False,
                             labels=[""]*len(top_s), colors=['gold']*len(top_s), opacity=[0.3]*len(top_s),
                             save=True, filepath='plots/topsimulationsP4.png')

In [207]:
plot_histograms_dict_overlay(dictionaries=top_simulated_data_P15,
                             true_data=referenceP15, bin_size=10,
                             plot_ref=True, true_label='Reference at P15',
                             title=f'ecDNA counts at Passage 15 and {top_percent}% best simulations (over {num_samples} samples) with {fitness} fitness',
                             plot_avg=True, avg_color='red',
                             confidence_level=5, CI_linecolor='orangered', CI_fillcolor='rgba(206, 255, 79, 0.2)',
                             plot_all=False,
                             labels=[""]*len(top_s), colors=['gold']*len(top_s), opacity=[0.3]*len(top_s),
                             save=True, filepath='plots/topsimulationsP15.png')